In [1]:
import numpy as np
import pandas as pd
pd.options.mode.chained_assignment = None
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import keras.backend as K
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from keras.wrappers.scikit_learn import KerasClassifier
import os
import random
import cv2
import keras
from keras.preprocessing.image import ImageDataGenerator
from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D, Dense, Dropout, Input, Flatten, Activation
from keras.layers import GlobalMaxPooling2D, Concatenate, concatenate
from keras.layers.normalization import BatchNormalization
from keras.layers.merge import Concatenate
from keras.models import Model
from keras.regularizers import l2
from keras import initializers
from keras.initializers import he_normal
from keras.optimizers import Adam
from keras.callbacks import ModelCheckpoint, Callback, EarlyStopping, ReduceLROnPlateau, TensorBoard

from scipy.ndimage import gaussian_filter
from skimage import img_as_float
from skimage.morphology import reconstruction

Using TensorFlow backend.


In [2]:
# Isolation function.
def iso(arr):
    #image = img_as_float(np.reshape(np.array(arr), [75, 75]))
    image = np.reshape(np.array(arr), [75, 75])
    image = gaussian_filter(image, 2.5)
    seed = np.copy(image)
    seed[1:-1, 1:-1] = image.min()
    mask = image 
    dilated = reconstruction(seed, mask, method='dilation')
    return image-dilated

def size(arr):
    p = np.reshape(np.array(arr), [75, 75]) > (np.mean(np.array(arr)) + 2*np.std(np.array(arr)))
    arr2 = p * np.reshape(np.array(arr), [75, 75])
    return np.sum(arr2 < -5)

def norm(x):
    x = np.array(x)
    return np.array((x - x.mean())/(x.max() - x.min()))

In [3]:
fileDataTrain = './train.json'

inputTrainRaw = pd.read_json(fileDataTrain)

inputTrainRaw.inc_angle.replace('na', 0, inplace=True)
inputTrainRaw.inc_angle = inputTrainRaw.inc_angle.astype(float).fillna(0.0)

inputTrain = inputTrainRaw[inputTrainRaw['inc_angle'] > 0]

inputTrain['band_3'] = [(np.array(b1) + np.array(b2))/2 for b1, b2 in zip(inputTrain['band_1'], inputTrain['band_2'])]

x_band1 = np.array([np.array(band).astype(np.float32).reshape(75, 75) for band in inputTrain["band_1"]])
x_band2 = np.array([np.array(band).astype(np.float32).reshape(75, 75) for band in inputTrain["band_2"]])
x_band3 = np.array([np.array(band).astype(np.float32).reshape(75, 75) for band in inputTrain["band_3"]])

# additional features
for band in ['band_1', 'band_2', 'band_3']:
    inputTrain[band+'_mean'] =   [np.mean(band) for band in inputTrain[band]]
    inputTrain[band+'_std'] =    [np.std(band) for band in inputTrain[band]]
    inputTrain[band+'_min'] =    [np.min(band) for band in inputTrain[band]]
    inputTrain[band+'_max'] =    [np.max(band) for band in inputTrain[band]]
    inputTrain[band+'_median'] = [np.median(band) for band in inputTrain[band]]
    inputTrain[band+'_size'] =   [size(band) for band in inputTrain[band]]
    
x_band1 = np.array([(x - x.mean())/(x.max() - x.min()) for x in x_band1])
x_band2 = np.array([(x - x.mean())/(x.max() - x.min()) for x in x_band2])
x_band3 = np.array([(x - x.mean())/(x.max() - x.min()) for x in x_band3])

x_data = np.concatenate([x_band1[:, :, :, np.newaxis], x_band2[:, :, :, np.newaxis], 
                         x_band3[:, :, :, np.newaxis]], axis=-1)

x_data_side = np.array(inputTrain[['inc_angle', 
                                   'band_1_min', 'band_1_max', 
                                   'band_2_min', 'band_2_max', 
                                   'band_1_size', 'band_2_size']])
x_data_side2 = x_data_side
for i in range(x_data_side.shape[1]):
    x_data_side2[:, i] = norm(x_data_side[:, i])

x_data_ang = np.array(inputTrain['inc_angle'])

x_data = np.array(x_data)

y_data = np.array(inputTrain['is_iceberg'])

x_train_ang = []

x_train, x_test, x_train_side, x_test_side, y_train, y_test = train_test_split(x_data, 
                                                                               x_data_side2, 
                                                                               y_data, 
                                                                               test_size=0.25, 
                                                                               random_state=2017)


print ('x_data:', np.shape(x_data))
print ('y_data:', np.shape(y_data))
print ('x_train:', np.shape(x_train))
print ('x_train_ang:', np.shape(x_train_side))
print ('y_train:', np.shape(y_train))
print ('x_test:', np.shape(x_test))
print ('x_test_ang:', np.shape(x_test_side))
print ('y_test:', np.shape(y_test))

x_data: (1471, 75, 75, 3)
y_data: (1471,)
x_train: (1103, 75, 75, 3)
x_train_ang: (1103, 7)
y_train: (1103,)
x_test: (368, 75, 75, 3)
x_test_ang: (368, 7)
y_test: (368,)


In [4]:
def convNN3_1(l2_rate=0.1, cnn_filter=32, cnn_drop=0.3, fcnn_drop=0.2):
    '''
    3rd version of convnet, 
    small number of conv filters, 
    extended 2nd input
    '''
    model = Sequential()
    
    # Input node for inc_angle
    side_input = Input(shape=(x_data_side.shape[1],), name='side_input')
    main_input = Input(shape=(75, 75, 3), name='main_input')
    
    ## FIRST BRANCH
    
    # Conv Layer 1
    conv1 = (Conv2D(cnn_filter, kernel_size=(3, 3),activation='relu', name='conv1_1'))(main_input)
    conv1 = (BatchNormalization(name='conv1_2'))(conv1)
    conv1 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv1_3'))(conv1)
    conv1 = (Dropout(cnn_drop, name='conv1_4'))(conv1)

    # Conv Layer 2
    conv2 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv2_1'))(conv1)
    conv2 = (BatchNormalization(name='conv2_2'))(conv2)
    conv2 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv2_3'))(conv2)
    conv2 = (Dropout(cnn_drop, name='conv2_4'))(conv2)

    # Conv Layer 3
    conv3 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv3_1'))(conv2)
    conv3 = (BatchNormalization(name='conv3_2'))(conv3)
    conv3 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv3_3'))(conv3)
    conv3 = (Dropout(cnn_drop, name='conv3_4'))(conv3)
       
    # Conv Layer 4
    conv4 = (Conv2D(cnn_filter, kernel_size=(3, 3), activation='relu', name='conv4_1'))(conv3)
    conv4 = (BatchNormalization(name='conv4_2'))(conv4)
    conv4 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv4_3'))(conv4)
    conv4 = (Dropout(cnn_drop, name='conv4_4'))(conv4)

    # Flatten the data for upcoming dense layers
    flat1 = Flatten(name='flat1')(conv4)
    
    ## 2ND BRANCH
    
    tower_1 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower1_1')(conv4)
    tower_1 = BatchNormalization()(tower_1)
    tower_1 = Conv2D(64, (3, 3), padding='same', activation='relu', name='tower1_2')(tower_1)
    tower_1 = Dropout(cnn_drop, name='tower1_3')(tower_1)

    tower_2 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower2_1')(conv4)
    tower_2 = BatchNormalization()(tower_2)
    tower_2 = Conv2D(64, (5, 5), padding='same', activation='relu', name='tower2_2')(tower_2)
    tower_2 = Dropout(cnn_drop, name='tower2_3')(tower_2)    

    tower_3 = MaxPooling2D((3, 3), strides=(1, 1), padding='same', name='tower3_1')(conv4)
    tower_3 = BatchNormalization()(tower_3)
    tower_3 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower3_2')(tower_3)
    tower_3 = Dropout(cnn_drop, name='tower3_3')(tower_3) 

    output1 = keras.layers.concatenate([tower_1, tower_2, tower_3], name='conc1')
    
    flat2 = (Flatten(name='flat2'))(output1)
    
    # Add inc_angle input
    model = Concatenate()([flat1, flat2, side_input])
    model = Dropout(fcnn_drop)(model)
        
    # Dense Layers
    model = Dense(512, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Dense Layer 2
    model = Dense(256, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Sigmoid Layer
    model = Dense(1)(model)
    output = Activation('sigmoid')(model)
    
    model = Model([main_input, side_input], output)

    optim = Adam(lr=0.001, decay=0.0)
        
    model.compile(loss = 'binary_crossentropy',
                  optimizer = optim,
                  metrics = ['accuracy'])
    return model, 'convNN3_1'

In [7]:
def convNN3_2(l2_rate=0.1, cnn_filter=32, cnn_drop=0.3, fcnn_drop=0.2):
    '''
    3rd version of convnet, 
    small number of conv filters, 
    extended 2nd input
    '''
    model = Sequential()
    
    # Input node for inc_angle
    side_input = Input(shape=(x_data_side.shape[1],), name='side_input')
    main_input = Input(shape=(75, 75, 3), name='main_input')
    
    ## FIRST BRANCH
    
    # Conv Layer 1
    conv1 = (Conv2D(cnn_filter, kernel_size=(3, 3),activation='relu', name='conv1_1'))(main_input)
    conv1 = (BatchNormalization(name='conv1_2'))(conv1)
    conv1 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv1_3'))(conv1)
    conv1 = (Dropout(cnn_drop, name='conv1_4'))(conv1)

    # Conv Layer 2
    conv2 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv2_1'))(conv1)
    conv2 = (BatchNormalization(name='conv2_2'))(conv2)
    conv2 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv2_3'))(conv2)
    conv2 = (Dropout(cnn_drop, name='conv2_4'))(conv2)

    # Conv Layer 3
    conv3 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv3_1'))(conv2)
    conv3 = (BatchNormalization(name='conv3_2'))(conv3)
    conv3 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv3_3'))(conv3)
    conv3 = (Dropout(cnn_drop, name='conv3_4'))(conv3)
       
    # Conv Layer 4
    conv4 = (Conv2D(cnn_filter, kernel_size=(3, 3), activation='relu', name='conv4_1'))(conv3)
    conv4 = (BatchNormalization(name='conv4_2'))(conv4)
    conv4 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv4_3'))(conv4)
    conv4 = (Dropout(cnn_drop, name='conv4_4'))(conv4)

    # Flatten the data for upcoming dense layers
    flat1 = Flatten(name='flat1')(conv4)
    '''
    ## 2ND BRANCH
    
    tower_1 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower1_1')(conv4)
    tower_1 = BatchNormalization()(tower_1)
    tower_1 = Conv2D(64, (3, 3), padding='same', activation='relu', name='tower1_2')(tower_1)
    tower_1 = Dropout(cnn_drop, name='tower1_3')(tower_1)

    tower_2 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower2_1')(conv4)
    tower_2 = BatchNormalization()(tower_2)
    tower_2 = Conv2D(64, (5, 5), padding='same', activation='relu', name='tower2_2')(tower_2)
    tower_2 = Dropout(cnn_drop, name='tower2_3')(tower_2)    

    tower_3 = MaxPooling2D((3, 3), strides=(1, 1), padding='same', name='tower3_1')(conv4)
    tower_3 = BatchNormalization()(tower_3)
    tower_3 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower3_2')(tower_3)
    tower_3 = Dropout(cnn_drop, name='tower3_3')(tower_3) 

    output1 = keras.layers.concatenate([tower_1, tower_2, tower_3], name='conc1')
    
    flat2 = (Flatten(name='flat2'))(output1)
    '''
    # Add inc_angle input
    model = Concatenate()([flat1, side_input])
    model = Dropout(fcnn_drop)(model)
        
    # Dense Layers
    model = Dense(512, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Dense Layer 2
    model = Dense(256, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Sigmoid Layer
    model = Dense(1)(model)
    output = Activation('sigmoid')(model)
    
    model = Model([main_input, side_input], output)

    optim = Adam(lr=0.001, decay=0.0)
        
    model.compile(loss = 'binary_crossentropy',
                  optimizer = optim,
                  metrics = ['accuracy'])
    return model, 'convNN3_2'

In [4]:
def convNN3_3(l2_rate=0.1, cnn_filter=32, cnn_drop=0.3, fcnn_drop=0.2, tower_drop=0.3, bn_pos=1):
    '''
    3rd version of convnet, 
    small number of conv filters, 
    extended 2nd input
    '''
    model = Sequential()
    
    # Input node for inc_angle
    side_input = Input(shape=(x_data_side.shape[1],), name='side_input')
    main_input = Input(shape=(75, 75, 3), name='main_input')
    
    ## FIRST BRANCH
    
    # Conv Layer 1
    conv1 = (Conv2D(cnn_filter, kernel_size=(3, 3),activation='relu', name='conv1_1'))(main_input)
    if bn_pos:
        conv1 = (BatchNormalization(name='conv1_2'))(conv1)
        conv1 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv1_3'))(conv1)
    else:
        conv1 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv1_3'))(conv1)
        conv1 = (BatchNormalization(name='conv1_2'))(conv1)
    conv1 = (Dropout(cnn_drop, name='conv1_4'))(conv1)

    # Conv Layer 2
    conv2 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv2_1'))(conv1)
    if bn_pos:
        conv2 = (BatchNormalization(name='conv2_2'))(conv2)
        conv2 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv2_3'))(conv2)
    else:
        conv2 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv2_3'))(conv2)
        conv2 = (BatchNormalization(name='conv2_2'))(conv2)
    conv2 = (Dropout(cnn_drop, name='conv2_4'))(conv2)

    # Conv Layer 3
    conv3 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv3_1'))(conv2)
    if bn_pos:
        conv3 = (BatchNormalization(name='conv3_2'))(conv3)
        conv3 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv3_3'))(conv3)
    else:
        conv3 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv3_3'))(conv3)
        conv3 = (BatchNormalization(name='conv3_2'))(conv3)
    conv3 = (Dropout(cnn_drop, name='conv3_4'))(conv3)
       
    # Conv Layer 4
    conv4 = (Conv2D(cnn_filter, kernel_size=(3, 3), activation='relu', name='conv4_1'))(conv3)
    if bn_pos:
        conv4 = (BatchNormalization(name='conv4_2'))(conv4)
        conv4 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv4_3'))(conv4)
    else:
        conv4 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv4_3'))(conv4)
        conv4 = (BatchNormalization(name='conv4_2'))(conv4)
    conv4 = (Dropout(cnn_drop, name='conv4_4'))(conv4)

    # Flatten the data for upcoming dense layers
    flat1 = Flatten(name='flat1')(conv4)
    
    ## 2ND BRANCH
    
    tower_1 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower1_1')(conv4)
    tower_1 = BatchNormalization()(tower_1)
    tower_1 = Conv2D(64, (3, 3), padding='same', activation='relu', name='tower1_2')(tower_1)
    tower_1 = Dropout(tower_drop, name='tower1_3')(tower_1)

    tower_2 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower2_1')(conv4)
    tower_2 = BatchNormalization()(tower_2)
    tower_2 = Conv2D(64, (5, 5), padding='same', activation='relu', name='tower2_2')(tower_2)
    tower_2 = Dropout(tower_drop, name='tower2_3')(tower_2)    

    tower_3 = MaxPooling2D((3, 3), strides=(1, 1), padding='same', name='tower3_1')(conv4)
    tower_3 = BatchNormalization()(tower_3)
    tower_3 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower3_2')(tower_3)
    tower_3 = Dropout(tower_drop, name='tower3_3')(tower_3) 

    output1 = keras.layers.concatenate([tower_1, tower_2, tower_3], name='conc1')
    
    flat2 = (Flatten(name='flat2'))(output1)
    
    # Add inc_angle input
    model = Concatenate()([flat1, flat2, side_input])
    model = Dropout(fcnn_drop)(model)
        
    # Dense Layers
    model = Dense(512, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Dense Layer 2
    model = Dense(256, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Sigmoid Layer
    model = Dense(1)(model)
    output = Activation('sigmoid')(model)
    
    model = Model([main_input, side_input], output)

    optim = Adam(lr=0.001, decay=0.0)
        
    model.compile(loss = 'binary_crossentropy',
                  optimizer = optim,
                  metrics = ['accuracy'])
    return model, 'convNN3_3'

In [4]:
def convNN3_4(l2_rate=0.1, cnn_filter=32, cnn_drop=0.3, 
              fcnn_drop=0.2, tower_drop=0.3, bn_pos=1, d1_size=512):
    '''
    3rd version of convnet, 
    small number of conv filters, 
    extended 2nd input
    '''
    model = Sequential()
    
    # Input node for inc_angle
    side_input = Input(shape=(x_data_side.shape[1],), name='side_input')
    main_input = Input(shape=(75, 75, 3), name='main_input')
    
    ## FIRST BRANCH
    
    # Conv Layer 1
    conv1 = (Conv2D(cnn_filter, kernel_size=(3, 3),activation='relu', name='conv1_1'))(main_input)
    if bn_pos:
        conv1 = (BatchNormalization(name='conv1_2'))(conv1)
        conv1 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv1_3'))(conv1)
    else:
        conv1 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv1_3'))(conv1)
        conv1 = (BatchNormalization(name='conv1_2'))(conv1)
    conv1 = (Dropout(cnn_drop, name='conv1_4'))(conv1)

    # Conv Layer 2
    conv2 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv2_1'))(conv1)
    if bn_pos:
        conv2 = (BatchNormalization(name='conv2_2'))(conv2)
        conv2 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv2_3'))(conv2)
    else:
        conv2 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv2_3'))(conv2)
        conv2 = (BatchNormalization(name='conv2_2'))(conv2)
    conv2 = (Dropout(cnn_drop, name='conv2_4'))(conv2)

    # Conv Layer 3
    conv3 = (Conv2D(cnn_filter*2, kernel_size=(3, 3), activation='relu', name='conv3_1'))(conv2)
    if bn_pos:
        conv3 = (BatchNormalization(name='conv3_2'))(conv3)
        conv3 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv3_3'))(conv3)
    else:
        conv3 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv3_3'))(conv3)
        conv3 = (BatchNormalization(name='conv3_2'))(conv3)
    conv3 = (Dropout(cnn_drop, name='conv3_4'))(conv3)
       
    # Conv Layer 4
    conv4 = (Conv2D(cnn_filter, kernel_size=(3, 3), activation='relu', name='conv4_1'))(conv3)
    if bn_pos:
        conv4 = (BatchNormalization(name='conv4_2'))(conv4)
        conv4 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv4_3'))(conv4)
    else:
        conv4 = (MaxPooling2D(pool_size=(2, 2), strides=(2, 2), name='conv4_3'))(conv4)
        conv4 = (BatchNormalization(name='conv4_2'))(conv4)
    conv4 = (Dropout(cnn_drop, name='conv4_4'))(conv4)

    # Flatten the data for upcoming dense layers
    flat1 = Flatten(name='flat1')(conv4)
    
    ## 2ND BRANCH
    
    tower_1 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower1_1')(conv4)
    tower_1 = BatchNormalization()(tower_1)
    tower_1 = Conv2D(64, (3, 3), padding='same', activation='relu', name='tower1_2')(tower_1)
    tower_1 = Dropout(tower_drop, name='tower1_3')(tower_1)

    tower_2 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower2_1')(conv4)
    tower_2 = BatchNormalization()(tower_2)
    tower_2 = Conv2D(64, (5, 5), padding='same', activation='relu', name='tower2_2')(tower_2)
    tower_2 = Dropout(tower_drop, name='tower2_3')(tower_2)    

    tower_3 = MaxPooling2D((3, 3), strides=(1, 1), padding='same', name='tower3_1')(conv4)
    tower_3 = BatchNormalization()(tower_3)
    tower_3 = Conv2D(64, (1, 1), padding='same', activation='relu', name='tower3_2')(tower_3)
    tower_3 = Dropout(tower_drop, name='tower3_3')(tower_3) 

    output1 = keras.layers.concatenate([tower_1, tower_2, tower_3], name='conc1')
    
    flat2 = (Flatten(name='flat2'))(output1)
    
    # Add inc_angle input
    model = Concatenate()([flat1, flat2, side_input])
    model = Dropout(fcnn_drop)(model)
        
    # Dense Layers
    model = Dense(d1_size, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Dense Layer 2
    model = Dense(256, kernel_regularizer=l2(l2_rate), activation='relu')(model)
    model = Dropout(fcnn_drop)(model)

    # Sigmoid Layer
    model = Dense(1)(model)
    output = Activation('sigmoid')(model)
    
    model = Model([main_input, side_input], output)

    optim = Adam(lr=0.001, decay=0.0)
        
    model.compile(loss = 'binary_crossentropy',
                  optimizer = optim,
                  metrics = ['accuracy'])
    return model, 'convNN3_4'

In [5]:
model, model_name = convNN3_4()
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
main_input (InputLayer)         (None, 75, 75, 3)    0                                            
__________________________________________________________________________________________________
conv1_1 (Conv2D)                (None, 73, 73, 32)   896         main_input[0][0]                 
__________________________________________________________________________________________________
conv1_2 (BatchNormalization)    (None, 73, 73, 32)   128         conv1_1[0][0]                    
__________________________________________________________________________________________________
conv1_3 (MaxPooling2D)          (None, 36, 36, 32)   0           conv1_2[0][0]                    
__________________________________________________________________________________________________
conv1_4 (D

In [23]:
def get_train_data(rotation_range=5, width_shift_range=0.2, 
                   height_shift_range=0.2, zoom_range=0.1,
                   flips=False, batch_size=32, 
                   data1=x_train, data2=x_train_ang, 
                   y_label=y_train):
    datagen = ImageDataGenerator(rotation_range = rotation_range, 
                                 width_shift_range = width_shift_range, 
                                 height_shift_range = height_shift_range, 
                                 zoom_range = zoom_range, 
                                 horizontal_flip = flips, 
                                 vertical_flip = flips)

    def generate_generator_multiple(generator, data1, data2, y_label, batch_size):
        genX1 = generator.flow(data1, y_label, 
                               batch_size=batch_size, 
                               shuffle=False)

        while True:
            for start in range(0, data2.shape[0], batch_size):
                X1i = genX1.next()       
                end = min(start + batch_size, data2.shape[0])
                y_out_batch = data2[start:end]

                yield [X1i[0], y_out_batch], X1i[1]

    inputgenerator=generate_generator_multiple(generator=datagen,
                                               data1=data1,
                                               data2=data2,
                                               y_label=y_label,
                                               batch_size=batch_size) 
    return inputgenerator



def get_callbacks():
    earlyStopping = EarlyStopping(monitor='val_loss', patience=300, 
                                  verbose=1, mode='min')
    mcp_save = ModelCheckpoint(tmp_name, save_best_only=True, 
                               monitor='val_loss', mode='min')
    reduce_lr_loss = ReduceLROnPlateau(monitor='val_loss', factor=0.75, 
                                       patience=40, verbose=1, epsilon=1e-4, 
                                       mode='min')
    return [earlyStopping, mcp_save, reduce_lr_loss]



def save_and_report(outStr, val_loss):
    ''' Rename saved model
    Naming pattern: w_<model_name>_<val_loss>.hdf'''
    new_name = './models3/w_' + model_name + '_' + val_loss + '.hdf'
    os.rename(tmp_name, new_name)
    print ('Model weights saved as: {}\nBest val_loss: {}'.format(new_name, val_loss)) 
    
    # Save report
    with open('learning_report.txt', 'a') as f:
        f.write('Model weights saved as: {}\nBest val_loss: {}\n'.format(new_name, val_loss))
        f.write(outStr)
    
    # save progression
    pd.DataFrame(out.history).to_csv(new_name[:-3] + 'csv')
    
    
def preparation():
    # Cleaning
    try:
        os.remove(tmp_name)
    except:
        pass  
    
    # print info
    outStr = (f'rotation_range: {rotation_range} \nwidth_shift_range: {width_shift_range} \n\
height_shift_range: {height_shift_range} \nzoom_range: {zoom_range}\n\
flips: {flips}\nBATCH_SIZE: {batch_size}\n\n\n')
    print ('\n\n --- NEW MODEL --- \n')
    print (outStr)
    return outStr

NameError: name 'x_train_ang' is not defined

In [6]:
for repeats in range(1000):
    model = None
    
    l2_rate = random.choice([0.001, 0.01, 0.1])
    cnn_filter = 32 + random.choice([-8, -6, -4, -2, 0, 2, 4, 6, 8])
    cnn_drop = 0.3 + 0.2*np.random.rand() #random.choice([0.35, 0.4, 0.45])
    tower_drop = 0.3 + 0.4*np.random.rand() #random.choice([0.4, 0.5, 0.6, 0.7])
    fcnn_drop = random.choice([0.2, 0.25, 0.3, 0.35, 0.4])
    d1_size = random.choice([512, 1024, 2048])
    bn_pos = 1 #random.choice([0, 1])
    model, model_name = convNN3_4(l2_rate=l2_rate, cnn_filter=cnn_filter, 
                                  cnn_drop=cnn_drop, fcnn_drop=fcnn_drop,
                                  bn_pos=bn_pos, tower_drop=tower_drop, 
                                  d1_size=d1_size)

    
    # Params
    rotation_range = np.random.randint(0, 6)
    width_shift_range = 0.001 + 0.001*np.random.rand()
    height_shift_range = 0.6933 + 0.1*np.random.rand()
    zoom_range = 0.090 + 0.01*np.random.rand()
    flips = False
    batch_size = 32
    
    '''
    # Params
    rotation_range = 0 #np.random.randint(0, 5)
    width_shift_range = 0.375244309663737   #np.random.rand()
    height_shift_range = 0.7023636179941954  #np.random.rand()
    zoom_range = 0.02972301468048797 #0.5*np.random.rand()
    flips = False
    batch_size = 32 #random.choice([16, 32])
    
    
    while (width_shift_range + height_shift_range > 1.2):
        width_shift_range = 0.9*np.random.rand()
        height_shift_range = 0.9*np.random.rand()        
    '''
    
    # Temporal name for model
    tmp_name = 'model_weights_tmp_name.hdf'

    outStr = ''
    outStr += f'l2_rate: {l2_rate}\n'
    outStr += f'cnn_filter: {cnn_filter}\n'
    outStr += f'cnn_drop: {cnn_drop}\n'
    outStr += f'fcnn_drop: {fcnn_drop}\n'
    outStr += f'tower_drop: {tower_drop}\n'
    outStr += f'bn_pos: {bn_pos}\n'
    outStr += f'd1_size: {d1_size}\n'
    print (outStr)
    outStr += preparation()
    print (model_name)

    inputgenerator = get_train_data(rotation_range = rotation_range, 
                                    width_shift_range = width_shift_range, 
                                    height_shift_range = height_shift_range, 
                                    zoom_range = zoom_range,
                                    flips = flips, 
                                    batch_size = batch_size, 
                                    data1 = x_train, 
                                    data2 = x_train_side, 
                                    y_label = y_train)

    earlyStopping, mcp_save, reduce_lr_loss = get_callbacks()

    try:
        out=model.fit_generator(inputgenerator, validation_data = ([x_test, x_test_side], y_test),
                                steps_per_epoch = int((len(x_train)/batch_size)*0.3), 
                                epochs = 2500, verbose = 1,
                                callbacks = [earlyStopping, mcp_save, reduce_lr_loss])
    except KeyboardInterrupt:
        model.load_weights('./model_weights_tmp_name.hdf')
        model_eval = model.evaluate([x_test, x_test_side], y_test)
        val_loss = str(model_eval[0])[:8] 
        save_and_report(outStr, val_loss)
        break
    
    val_loss = (str(mcp_save.best))[:8]
    save_and_report(outStr, val_loss)   

l2_rate: 0.001
cnn_filter: 34
cnn_drop: 0.33919657472507614
fcnn_drop: 0.25
tower_drop: 0.36882934876367357
bn_pos: 1
d1_size: 1024



 --- NEW MODEL --- 

rotation_range: 3 
width_shift_range: 0.0016137712468051188 
height_shift_range: 0.7834692656369571 
zoom_range: 0.0958913504171586
flips: False
BATCH_SIZE: 32



convNN3_4
Epoch 1/2500
10/10 [==============================] - 6s 606ms/step - loss: 2.2678 - acc: 0.5719 - val_loss: 2.0555 - val_acc: 0.5353
Epoch 2/2500
10/10 [==============================] - 1s 64ms/step - loss: 2.1179 - acc: 0.5875 - val_loss: 1.9948 - val_acc: 0.5353
Epoch 3/2500
10/10 [==============================] - 1s 62ms/step - loss: 1.9839 - acc: 0.6063 - val_loss: 1.9736 - val_acc: 0.5353
Epoch 4/2500
10/10 [==============================] - 1s 60ms/step - loss: 1.9413 - acc: 0.6697 - val_loss: 2.0581 - val_acc: 0.5353
Epoch 5/2500
10/10 [==============================] - 1s 65ms/step - loss: 1.8863 - acc: 0.6125 - val_loss: 1.9254 - val_acc: 0.5353
Epoch

Epoch 59/2500
10/10 [==============================] - 1s 58ms/step - loss: 0.6895 - acc: 0.7906 - val_loss: 2.1417 - val_acc: 0.5707
Epoch 60/2500
10/10 [==============================] - 1s 54ms/step - loss: 0.6421 - acc: 0.8334 - val_loss: 3.6268 - val_acc: 0.5408
Epoch 61/2500
10/10 [==============================] - 1s 58ms/step - loss: 0.6743 - acc: 0.7750 - val_loss: 2.2387 - val_acc: 0.5761
Epoch 62/2500
10/10 [==============================] - 1s 63ms/step - loss: 0.6861 - acc: 0.7969 - val_loss: 1.1566 - val_acc: 0.6005
Epoch 63/2500
10/10 [==============================] - 1s 61ms/step - loss: 0.5802 - acc: 0.8365 - val_loss: 1.3347 - val_acc: 0.5924
Epoch 64/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.6308 - acc: 0.7875 - val_loss: 2.1050 - val_acc: 0.5625
Epoch 65/2500
10/10 [==============================] - 1s 58ms/step - loss: 0.6712 - acc: 0.7750 - val_loss: 1.3243 - val_acc: 0.6141
Epoch 66/2500
10/10 [==============================] - 1s 64ms

Epoch 120/2500
10/10 [==============================] - 1s 58ms/step - loss: 0.5203 - acc: 0.7750 - val_loss: 0.4384 - val_acc: 0.8370
Epoch 121/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.4806 - acc: 0.7812 - val_loss: 0.5716 - val_acc: 0.7717
Epoch 122/2500
10/10 [==============================] - 1s 59ms/step - loss: 0.4486 - acc: 0.8000 - val_loss: 0.4941 - val_acc: 0.8342
Epoch 123/2500
10/10 [==============================] - 1s 55ms/step - loss: 0.4615 - acc: 0.8239 - val_loss: 0.3892 - val_acc: 0.8451
Epoch 124/2500
10/10 [==============================] - 1s 57ms/step - loss: 0.4893 - acc: 0.7875 - val_loss: 0.5009 - val_acc: 0.7908
Epoch 125/2500
10/10 [==============================] - 1s 57ms/step - loss: 0.4827 - acc: 0.7937 - val_loss: 0.3770 - val_acc: 0.8478
Epoch 126/2500
10/10 [==============================] - 1s 63ms/step - loss: 0.3961 - acc: 0.8428 - val_loss: 0.4178 - val_acc: 0.8451
Epoch 127/2500
10/10 [==============================] -

Epoch 181/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.3873 - acc: 0.8219 - val_loss: 0.3352 - val_acc: 0.8533
Epoch 182/2500
10/10 [==============================] - 1s 71ms/step - loss: 0.3614 - acc: 0.8364 - val_loss: 0.2980 - val_acc: 0.8614
Epoch 183/2500
10/10 [==============================] - 1s 59ms/step - loss: 0.4014 - acc: 0.8031 - val_loss: 0.4122 - val_acc: 0.8451
Epoch 184/2500
10/10 [==============================] - 1s 57ms/step - loss: 0.4054 - acc: 0.8063 - val_loss: 0.3348 - val_acc: 0.8668
Epoch 185/2500
10/10 [==============================] - 1s 55ms/step - loss: 0.3861 - acc: 0.8438 - val_loss: 0.3820 - val_acc: 0.8424
Epoch 186/2500
10/10 [==============================] - 1s 59ms/step - loss: 0.4056 - acc: 0.8207 - val_loss: 0.3410 - val_acc: 0.8723
Epoch 187/2500
10/10 [==============================] - 1s 57ms/step - loss: 0.4040 - acc: 0.8063 - val_loss: 0.4366 - val_acc: 0.8424
Epoch 188/2500
10/10 [==============================] -

Epoch 242/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.3306 - acc: 0.8680 - val_loss: 0.3153 - val_acc: 0.8804
Epoch 243/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.3942 - acc: 0.8281 - val_loss: 0.3738 - val_acc: 0.8424
Epoch 244/2500
10/10 [==============================] - 1s 58ms/step - loss: 0.3542 - acc: 0.8375 - val_loss: 0.2524 - val_acc: 0.8886
Epoch 245/2500
10/10 [==============================] - 1s 66ms/step - loss: 0.2735 - acc: 0.8901 - val_loss: 0.2471 - val_acc: 0.8967
Epoch 246/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.3707 - acc: 0.8313 - val_loss: 0.3189 - val_acc: 0.8777
Epoch 247/2500
10/10 [==============================] - 1s 58ms/step - loss: 0.3943 - acc: 0.8063 - val_loss: 0.3940 - val_acc: 0.8587
Epoch 248/2500
10/10 [==============================] - 1s 56ms/step - loss: 0.3463 - acc: 0.8625 - val_loss: 0.6547 - val_acc: 0.8071
Epoch 249/2500
10/10 [==============================] -

...

Epoch 636/2500
10/10 [==============================] - 1s 69ms/step - loss: 0.1448 - acc: 0.9500 - val_loss: 0.2528 - val_acc: 0.9130
Epoch 637/2500
10/10 [==============================] - 1s 73ms/step - loss: 0.1222 - acc: 0.9466 - val_loss: 0.2462 - val_acc: 0.9185
Epoch 638/2500
10/10 [==============================] - 1s 65ms/step - loss: 0.1613 - acc: 0.9344 - val_loss: 0.2423 - val_acc: 0.9266
Epoch 639/2500
10/10 [==============================] - 1s 64ms/step - loss: 0.1545 - acc: 0.9469 - val_loss: 0.2418 - val_acc: 0.9239
Epoch 640/2500
10/10 [==============================] - 1s 63ms/step - loss: 0.1588 - acc: 0.9531 - val_loss: 0.2368 - val_acc: 0.9212
Epoch 641/2500
10/10 [==============================] - 1s 62ms/step - loss: 0.1735 - acc: 0.9246 - val_loss: 0.2399 - val_acc: 0.9212
Epoch 642/2500
10/10 [==============================] - 1s 63ms/step - loss: 0.1735 - acc: 0.9500 - val_loss: 0.2362 - val_acc: 0.9293
Epoch 643/2500
10/10 [==============================] -

10/10 [==============================] - 1s 82ms/step - loss: 0.8911 - acc: 0.7531 - val_loss: 1.2015 - val_acc: 0.6196
Epoch 67/2500
10/10 [==============================] - 1s 66ms/step - loss: 0.8285 - acc: 0.7924 - val_loss: 1.3265 - val_acc: 0.6114
Epoch 68/2500
10/10 [==============================] - 1s 66ms/step - loss: 0.8399 - acc: 0.7500 - val_loss: 1.4943 - val_acc: 0.6060
Epoch 69/2500
10/10 [==============================] - 1s 87ms/step - loss: 0.8159 - acc: 0.7875 - val_loss: 1.1704 - val_acc: 0.6304
Epoch 70/2500
10/10 [==============================] - 1s 75ms/step - loss: 0.7475 - acc: 0.8113 - val_loss: 1.2665 - val_acc: 0.6196
Epoch 71/2500
10/10 [==============================] - 1s 67ms/step - loss: 0.7831 - acc: 0.7562 - val_loss: 2.1123 - val_acc: 0.5489
Epoch 72/2500
10/10 [==============================] - 1s 65ms/step - loss: 0.8159 - acc: 0.7656 - val_loss: 1.3821 - val_acc: 0.6168
Epoch 73/2500
10/10 [==============================] - 1s 84ms/step - loss: 

10/10 [==============================] - 1s 66ms/step - loss: 0.5656 - acc: 0.7875 - val_loss: 0.5869 - val_acc: 0.7799
Epoch 128/2500
10/10 [==============================] - 1s 69ms/step - loss: 0.5646 - acc: 0.7875 - val_loss: 0.6939 - val_acc: 0.7418
Epoch 129/2500
10/10 [==============================] - 1s 81ms/step - loss: 0.5503 - acc: 0.7937 - val_loss: 0.4943 - val_acc: 0.8071
Epoch 130/2500
10/10 [==============================] - 1s 66ms/step - loss: 0.5491 - acc: 0.7861 - val_loss: 0.5274 - val_acc: 0.7745
Epoch 131/2500
10/10 [==============================] - 1s 66ms/step - loss: 0.6070 - acc: 0.7688 - val_loss: 0.5598 - val_acc: 0.7663
Epoch 132/2500
10/10 [==============================] - 1s 81ms/step - loss: 0.5464 - acc: 0.7875 - val_loss: 0.4895 - val_acc: 0.7962
Epoch 133/2500
10/10 [==============================] - 1s 76ms/step - loss: 0.5098 - acc: 0.8144 - val_loss: 0.5298 - val_acc: 0.8043
Epoch 134/2500
10/10 [==============================] - 1s 67ms/step -

Epoch 188/2500
10/10 [==============================] - 1s 69ms/step - loss: 0.4597 - acc: 0.7812 - val_loss: 0.4545 - val_acc: 0.7636
Epoch 189/2500
10/10 [==============================] - 1s 74ms/step - loss: 0.3936 - acc: 0.8049 - val_loss: 0.4655 - val_acc: 0.8098
Epoch 190/2500
10/10 [==============================] - 1s 67ms/step - loss: 0.4766 - acc: 0.7875 - val_loss: 0.7720 - val_acc: 0.6929
Epoch 191/2500
10/10 [==============================] - 1s 65ms/step - loss: 0.5344 - acc: 0.7844 - val_loss: 0.7335 - val_acc: 0.6332
Epoch 192/2500
10/10 [==============================] - 1s 65ms/step - loss: 0.4489 - acc: 0.8219 - val_loss: 0.4637 - val_acc: 0.7636
Epoch 193/2500
10/10 [==============================] - 1s 64ms/step - loss: 0.4498 - acc: 0.8397 - val_loss: 0.6329 - val_acc: 0.7962
Epoch 194/2500
10/10 [==============================] - 1s 65ms/step - loss: 0.4791 - acc: 0.7750 - val_loss: 0.6383 - val_acc: 0.7500
Epoch 195/2500
10/10 [==============================] -

Epoch 249/2500
10/10 [==============================] - 1s 69ms/step - loss: 0.3742 - acc: 0.8428 - val_loss: 0.4665 - val_acc: 0.8234
Epoch 250/2500
10/10 [==============================] - 1s 65ms/step - loss: 0.4710 - acc: 0.7656 - val_loss: 0.7142 - val_acc: 0.7663
Epoch 251/2500
10/10 [==============================] - 1s 68ms/step - loss: 0.4186 - acc: 0.7969 - val_loss: 0.6007 - val_acc: 0.7717
Epoch 252/2500
 8/10 [=======================>......] - ETA: 0s - loss: 0.3518 - acc: 0.8477
Epoch 00252: reducing learning rate to 0.0005625000048894435.
10/10 [==============================] - 1s 79ms/step - loss: 0.3512 - acc: 0.8459 - val_loss: 0.6001 - val_acc: 0.7799
Epoch 253/2500
10/10 [==============================] - 1s 67ms/step - loss: 0.4393 - acc: 0.7875 - val_loss: 0.5599 - val_acc: 0.7799
Epoch 254/2500
10/10 [==============================] - 1s 66ms/step - loss: 0.4110 - acc: 0.8094 - val_loss: 0.4715 - val_acc: 0.7935
Epoch 255/2500
10/10 [============================